In [1]:
!bkill -u ohoidn 0

Job <15488> is being terminated
Job <15490> is being terminated
Job <15492> is being terminated
Job <15494> is being terminated


In [1]:
#%matplotlib inline
%matplotlib nbagg
import config

#config.peak_width = 0.25 # Change from default value of 1.5.

from dataccess.nbfunctions import *
from dataccess import utils, query, mec, datashow
from dataccess.summarymetrics import plt, histogram, scatter
import config

from scipy.stats import pearsonr
from scipy import stats
from dataccess.peakfinder import peakfilter_frame
from scipy.ndimage.filters import gaussian_filter as gfilt
from scipy.interpolate import interp1d
from dataccess.xtcav import autocorrelation
from dataccess import mec
%pdb

711092
711093
711094
711095
Automatic pdb calling has been turned ON


In [2]:
#rm -r cache/*

In [3]:
from dataccess import peakfinder

def my_200_array(arr, bgsub = False, **kwargs):
    from dataccess import xrd
    from dataccess.peakfinder import peakfilter_frame
    dss = xrd.Pattern.from_dataset(arr, 'quad2', ['MgO'], frame_processor = peakfilter_frame, label  = 'test')
    return dss.peak_sizes(method = 'integral')[1]

def background(arr, **kwargs):
    dss = xrd.Pattern.from_dataset(arr, 'quad2', ['MgO'], frame_processor = peakfilter_frame, label  = 'test')
    return dss.background()

def display_good_events(ds):
    result = scatter(ds, ('quad2', background), ('quad2', my_200_array), plot = False,
        show = False, frame_processor = peakfilter_frame)
    edf = result.make_mask_dictionary(make_event_filter(result))
    a, b = result.apply_mask_dictionary(edf)
    plt.scatter(*result, label = ds.label)
    plt.scatter(a, b, label = ds.label)
    plt.ylabel('I200')
    plt.xlabel('I0')
    plt.show()

def reject_below(arr1d, n_std = 1.):
    threshold = np.mean(arr1d) - n_std * np.std(arr1d)
    return arr1d > threshold

def reject_above(arr1d, n_std = 1.):
    threshold = np.mean(arr1d) + n_std * np.std(arr1d)
    return arr1d < threshold

def make_event_mask(bg, i200):
    epsilon = 1e-5
    ratio = i200/(bg + epsilon)
    mask_below = reject_below(ratio, n_std = 0.5)
    mask_above = reject_above(ratio, n_std = 2)
    #mask_below_i200 = reject_below(i200, n_std = 1)
    mask_above_bg = reject_above(bg, n_std = 2)
    mask_above_i200 = reject_above(i200, n_std = 2)
    return mask_below & mask_above & mask_above_bg & mask_above_i200
    
def make_event_filter(scatter_data):
    arr_bg, arr_i200 = scatter_data
    epsilon = 1e-5
    arr_ratio = arr_i200/(arr_bg + epsilon)
    
    def reject_below(arr1d, val, n_std = 1.5):
        threshold = np.mean(arr1d) - n_std * np.std(arr1d)
        return val > threshold

    def reject_above(arr1d, val, n_std = 1.5):
        threshold = np.mean(arr1d) + n_std * np.std(arr1d)
        return val < threshold

    def event_filter(bg, i200):
        ratio = i200/(bg + epsilon)
        mask_below = reject_below(arr_ratio, ratio, n_std = 1.)
        mask_above = reject_above(arr_ratio, ratio, n_std = 1.5)
        #mask_below_i200 = reject_below(i200, n_std = 1)
        mask_above_bg = reject_above(arr_bg, bg, n_std = 1.5)
        mask_above_i200 = reject_above(arr_i200, i200, n_std = 1.5)
        mask_below_bg = reject_below(arr_bg, bg, n_std = 1.)
        mask_below_i200 = reject_below(arr_i200, i200, n_std = 1.)
        return mask_below & mask_above & mask_above_bg & mask_above_i200 & mask_below_bg & mask_below_i200
    return event_filter

from dataccess import peakfinder

def peakfilter_frame_histogram_lowthreshold(arr, detid = None, window_min = 0, radius = 4, thr_low = 5, thr_high = 10):
    """
    Mutates arr.
    """
    def filtfunc2(arr):
        base = 0#np.median(arr)
        return peakfinder.consolidate_peaks(arr, thr_low = thr_low, thr_high = thr_high, radius = radius)
    def process_island2(subarr):
        subarr[:] -= np.percentile(subarr, 20)
        subarr[:] = filtfunc2(subarr)
        return subarr
    
    if detid == 'quad2':
        clusters = clusters2
    elif detid == 'quad1':
        clusters = clusters1
    elif detid == 'si':
        return arr
    else:
        raise ValueError
    subregions = clustermap(arr, clusters, process_island2)
    for cluster, subarr in zip(clusters, subregions):
        bounding_view(arr, cluster)[:] = subarr
    arr[arr < window_min] = 0
    x, y = np.histogram(arr, bins = 100, range = (0, 300))
    return np.array([x, y[:-1]])

def decluster_and_mask(arr, detid = None):
    return mask2 * peakfilter_frame(arr, detid = detid)

def decluster_and_mask1(arr, detid = None):
    return mask1 * peakfilter_frame(arr, detid = detid)

%run ../masks/masks.py
mask2 = np.load('../masks/quad2_mask_10.11.npy')
mask1 = np.load('../masks/quad1_mask_10.11.npy')
arr1, clusters1 = find_islands(mask1, 0, 1000)
arr2, clusters2 = find_islands(mask2, 0, 1000)


def print_param(xrdset, param):
    for p in xrdset.patterns:
        peaks = p.peaks.peaks
        print [pk.param_values[param] for pk in peaks]
        
def histogram(arr, **kwargs):
    x, y = np.histogram(arr, bins = 100, range = (0, 300))
    return np.array([x, y[:-1]])

def plot_histogram(ds, ylim = None, show = True, label = '', **kwargs):
    dr = ds.evaluate('quad2', frame_processor = histogram)
    plt.xlabel('pixel value (ADU)')
    plt.ylabel('occurences per frame')
    x, y = dr.mean[::-1]
    if ylim is not None:
        plt.ylim(ylim)
    plt.plot(x, y, label = label, **kwargs)
    if show:
        plt.show()

In [4]:
def plot_xrd_masked(datasets, event_masks, mode = 'patterns', peak_widths = {0: 1.5, 1: 1.5, 2: 1.5, 3: 1.7}, 
                    param_initial_values = {3: {'sigma': (0.4, False), 'amplitude': (5., False), 'center': (129.7, True)},
                                   1: {'amplitude': (30, False)}},
                    iter_parameters = {'sigma': [3]}, normalization = 'peak', **kwargs):
    if mode == 'patterns':
        plot_patterns, plot_progression = True, False
    elif mode == 'progression':
        plot_patterns, plot_progression = False, True
    else:
        raise ValueError
    return plot_xrd(datasets, compound_list = ['MgO'], normalization = normalization,
         plot_patterns = plot_patterns,  plot_progression = plot_progression, show_image = False,
         detectors = ['quad2', 'quad1'],
         frame_processor = peakfilter_frame, peak_widths = peak_widths,
            iter_parameters = iter_parameters,
            param_initial_values = param_initial_values,
            event_masks = event_masks, **kwargs)

def plot_xrd_masked_nth_bin(datasets, bin_index, num_bins = 3, mode = 'patterns', **kwargs):
    assert bin_index < num_bins
    masks = [dataset_get_i200_i00_dictionary_masks(ds, num_bins)[bin_index] for ds in datasets]
    return plot_xrd_masked(datasets, masks, mode = mode, **kwargs)

In [5]:
def xrd_events_spaghetti(dataset, start_index, end_index):
    nevents = dataset.evaluate('quad2').nevents()
    def mask_n(n):
        return {dataset.runs[0]: {k: (True if k == n else False) for k in range(nevents)}}

    masks = [mask_n(i) for i in range(nevents)]

    plot_xrd_masked([dataset] * (end_index - start_index), masks[start_index:end_index], mode = 'patterns', normalization = None)

In [6]:
MgO_ref_short_full = [query.DataSet([906], label = 'MgO.ref.1C.short.2um')] + [get_query_dataset('material MgO runs 870 961 transmission 1. focal_size %d' % spotsize,
                                'MgO.ref.1C.short2.%sum' % spotsize, print_enable = False)
                                for spotsize in [4, 8, 18, 38, 48]] + [query.DataSet([922], label = 'MgO.ref.1C.short.58um')]
MgO_ref_short_clean = [get_query_dataset('material MgO runs 870 961 transmission 1. focal_size %d' % spotsize,
                                'MgO.ref.1C.short.%sum' % spotsize, print_enable = False)
                                for spotsize in [4, 8, 18, 38, 48]] + [query.DataSet([922], label = 'MgO.ref.1C.short.58um')]
datasets = MgO_ref_short_full
ds = datasets[1]

In [7]:
def mask_n(n):
    return {911: {k: (True if k == n else False) for k in range(696)}}
masks = [mask_n(i) for i in range(696)]
n, m = 0, 10
plot_xrd_masked([ds] * (m - n), masks[n:m], mode = 'patterns')

<dataccess.xrd.XRD instance at 0x7feae806ad88>

In [8]:
def cm_200_3(arr, bgsub = False, **kwargs):
    from dataccess import xrd
    dss = xrd.Pattern.from_dataset(arr, 'quad2', ['MgO'], label  = 'test')
    return dss.centers_of_mass()[1]

In [9]:
from dataccess import api

@api.register_input_detids('quad2', 'si')
def pair(quad2 = None, si = None):
    cleaned_quad2 = peakfilter_frame(quad2, detid = 'quad2')
    cm_200 = cm_200_3(cleaned_quad2)
    cm_si = mec.si_imarr_cm_3(si)
    return (cm_200, cm_si)

In [10]:
from dataccess import api

def powder_pattern_no_correction(imarr = None, **kwargs):
    from dataccess import xrd
    import numpy as np
    from dataccess.peakfinder import peakfilter_frame
    pat = xrd.Pattern.from_dataset(peakfilter_frame(imarr, detid = 'quad2'), 'quad2', ['MgO'], label  = 'test')
    #pdb.set_trace()
    return pat.angles, pat.intensities

def powder_pattern_shift_cm5(imarr = None, **kwargs):
    from dataccess import xrd
    import numpy as np
    from dataccess.peakfinder import peakfilter_frame
    pat = xrd.Pattern.from_dataset(peakfilter_frame(imarr, detid = 'quad2'), 'quad2', ['MgO'], label  = 'test')
    return np.array(pat.recentered_peaks())

def powder_pattern_cm(imarr = None, **kwargs):
    import numpy as np
    from dataccess.peakfinder import peakfilter_frame
    from dataccess import xrd
    dss = xrd.Pattern.from_dataset(peakfilter_frame(imarr, detid = 'quad2'), 'quad2', ['MgO'], label  = 'test')
    return dss.centers_of_mass()[1]

from dataccess import api

nominal_energy = 8965.
@api.register_input_detids('quad2', 'si')
def powder_pattern_evt_2(quad2 = None, si = None, **kwargs):
    from dataccess import xrd
    import numpy as np
    from dataccess.peakfinder import peakfilter_frame
    from dataccess import mec
    cleaned_quad2 = peakfilter_frame(quad2, detid = 'quad2')
    pat = xrd.Pattern.from_dataset(cleaned_quad2, 'quad2', ['MgO'], label  = 'test')
    cm_si = mec.si_imarr_cm_3(si)
    deltaE = cm_si - nominal_energy
    theta_rad = np.deg2rad(pat.angles)
    theta_correction = np.rad2deg(2 * np.tan(theta_rad/2) * deltaE/nominal_energy)
    rescale = (pat.angles + theta_correction)/pat.angles
    angles, intensities = utils.regrid(pat.angles, pat.intensities, rescale)
    return np.array([angles, intensities])


In [11]:
def nearest_max(arr1d, index, smooth = 1):
    from scipy.signal import argrelextrema
    from scipy.ndimage.filters import gaussian_filter as gfilt
    i_max = argrelextrema(gfilt(arr1d, smooth), np.greater)[0]
    i_closest = np.abs(i_max - index).argmin()
    return i_max[i_closest]

def dataresult_to_pattern(dataresult, compound_list = ['MgO']):
    mean_angles, mean_intensities = dataresult.mean
    return xrd.Pattern(mean_angles, mean_intensities, compound_list)

def peak_angles(dataresult, compound_list = ['MgO']):
    """
    dataresult : DataResult instance with each value in dataresult.event_data a spectrum of the form [x, y]
    """
    mean_angles, mean_intensities = dataresult.mean
    def peak_nominal_index(peak):
        indices = peak.crop_indices(mean_angles, peak.peak_width)
        return indices[len(indices)/2]
    pattern = dataresult_to_pattern(dataresult, compound_list = compound_list)
    nominal_peak_indices = [peak_nominal_index(peak) for peak in pattern.peaks.peaks]
    indices = [nearest_max(mean_intensities, i) for i in nominal_peak_indices]
    return [mean_angles[i] for i in indices]

def peak_cms(dataresult, compound_list = ['MgO']):
    from copy import deepcopy
    dataresult_copy = deepcopy(dataresult)
    pattern = dataresult_to_pattern(dataresult_copy, compound_list = compound_list)
    pattern_angles, pattern_intensities = dataresult_copy.mean
    angles = peak_angles(dataresult_copy, compound_list = compound_list)
    for angle, peak in zip(angles, pattern.peaks.peaks):
        peak.angle = angle
    #pdb.set_trace()
    return [peak.center_of_mass(pattern_angles, pattern_intensities) for peak in pattern.peaks.peaks]

def powder_pattern_shift_customize_angle(peak_angles = None, shift_scale = -1.):
    def frame_processor(imarr = None, **kwargs):
        from dataccess import xrd
        import numpy as np
        from dataccess.peakfinder import peakfilter_frame
        pat = xrd.Pattern.from_dataset(peakfilter_frame(imarr, detid = 'quad2'), 'quad2', ['MgO'],
                                       label  = 'test', peak_angles = peak_angles)
        return np.array(pat.recentered_peaks(shift_scale = shift_scale))
    return frame_processor

def powder_pattern_shift_iterate_cm(dataset, shift_scale = -1.):
    uncorrected = dataset.evaluate('quad2', frame_processor = powder_pattern_no_correction, event_data_getter = utils.identity)
    peak_angles = peak_cms(uncorrected, compound_list = ['MgO'])
    return dataset.evaluate('quad2', frame_processor =
                            powder_pattern_shift_customize_angle(peak_angles = peak_angles, shift_scale = shift_scale))

def shift_iterate_cm_pattern(dataset, shift_scale = -1):
    result = powder_pattern_shift_iterate_cm(dataset)
    pattern = dataresult_to_pattern(result)
    pattern.label = dataset.label
    return pattern

In [12]:
def plot_cm_progression_shifted(datasets):
    for d in datasets:
        result = powder_pattern_shift_iterate_cm(d)
        pattern = dataresult_to_pattern(result)
        pattern.label = d.label
        cms = np.array(peak_cms(result))
        plt.plot(cms, label = d.label)

In [13]:
peaksizes = ds.evaluate('quad2', frame_processor = my_200_array, event_data_getter = utils.identity)

### Peak CM vs. event number during linear raster:

In [14]:
trace = ds.evaluate('quad2', frame_processor = powder_pattern_cm, event_data_getter = utils.identity)
event_numbers, cms = range(len(trace.flat_event_data())), trace.flat_event_data()
smoothed_cm_interp = utils.extrap1d(interp1d(event_numbers, gfilt(cms, 20)))
smoothed_cms = smoothed_cm_interp(event_numbers)
cms_highpass = cms - smoothed_cms
from dataccess.mec import si_imarr_cm_3
energies = ds.evaluate('si', frame_processor = si_imarr_cm_3, event_data_getter = utils.identity)

plt.scatter(event_numbers, cms, label = 'raw')
plt.plot(np.array(event_numbers), smoothed_cms, label  ='interpolation, smoothed with sigma = 20')
plt.show()

### Scatter plot of 200 peak position vs XFEL energy, with and without subtraction of low-frequency variation due to sample unevenness:

In [15]:
plt.scatter(cms, energies.flat_event_data(), label = 'raw')
plt.scatter(cms_highpass + np.mean(cms), energies.flat_event_data(), label = 'low-frequency variation removed')
plt.show()

### Plot the progression of powder peak positions as a function of flux:

In [16]:
fluxes = np.array([xrd.get_flux_density(d) for d in datasets])
shifted_results = map(powder_pattern_shift_iterate_cm, datasets)
cm_progression = np.array(map(peak_cms, shifted_results))

In [17]:
f, axlist = plt.subplots(1)
ax = axlist[0]
ax.set_xlabel('Flux density(J/cm^s)')
ax.set_ylabel('rel. peak angle (normalized to min flux)')
ax.set_xscale('log')
[ax.plot(fluxes, p/p[-1], label = lab) for p, lab in zip(cm_progression.T, ['111', '200', '220'])]
plt.show()

### Remove event-to-event peak position jitter:

In [18]:
uncorrected = ds.evaluate('quad2', frame_processor = powder_pattern_no_correction, event_data_getter = utils.identity)
cmshift = ds.evaluate('quad2', frame_processor = powder_pattern_shift_cm5, event_data_getter = utils.identity)
shifted2 = powder_pattern_shift_iterate_cm(ds)
plt.plot(*uncorrected.mean, label = 'peak position jitter: not corrected')
plt.plot(*cmshift.mean, label = 'peak position jitter: corrected')
plt.plot(*shifted2.mean, label = 'peak position jitter: corrected and centered')

plt.show()

### Plot powder peaks for all flux densities:

In [19]:
def plot_one(res, label):
    plt.plot(res.mean[0], res.mean[1]/np.max(res.mean[1][590:610]), label = label)

In [20]:
for res, label in zip(shifted_results, [d.label for d in datasets]):
    plot_one(res, label)
plt.show()

### Revised peak intensity estimation:

* No more peak-fitting
* simple integral with third-order polynomial fit to background

In [21]:
plot_xrd(datasets[:1], compound_list = ['MgO'], normalization = 'integral_bgsubbed',
         plot_patterns = True,  show_image = False, detectors = ['quad2', 'quad1'],
         frame_processor = peakfilter_frame)

<dataccess.xrd.XRD instance at 0x7feadb266e60>

In [22]:
plot_xrd(datasets, compound_list = ['MgO'], normalization = 'integral_bgsubbed',
         plot_patterns = False,  plot_progression = True, show_image = False, detectors = ['quad2', 'quad1'],
         frame_processor = peakfilter_frame)

<dataccess.xrd.XRD instance at 0x7feadb240c20>

In [23]:
plot_xrd(datasets, compound_list = ['MgO'], normalization = None,
         plot_patterns = False,  plot_progression = True, show_image = False, detectors = ['quad2', 'quad1'],
         frame_processor = peakfilter_frame)

<dataccess.xrd.XRD instance at 0x7feadb3037a0>

In [ ]:
xrd_events_spaghetti(ds, 0, 10)

### Compare powder patterns with and without correction for XFEL energy jitter

In [ ]:
res2 = ds.evaluate('quad2', frame_processor = powder_pattern_no_correction, event_data_getter = utils.identity)
res3 = ds.evaluate('quad2', frame_processor = powder_pattern_evt_2, event_data_getter = utils.identity)

engine batch:  711092
Waiting for engines...
_get_view timed out.
Could not obtain batch engine. Attempting to run on local host
[32] > /reg/neh/home5/ohoidn/venv_test/mecana2/lib/python2.7/site-packages/dataccess-1.0-py2.7.egg/dataccess/batchjobs.py(98)start_engines()
-> subprocess.Popen('mpirun -n {0} ipengine --profile={1} --log-to-file 2>&1 &'.format(min(ncores, LOCAL_NCORES), name),


In [ ]:
plt.plot(np.mean(np.array(list(res2.iter_event_value_pairs()))[:, 1], axis = 0), label = '') # not corrected
plt.plot(np.mean(np.array(list(res3.iter_event_value_pairs()))[:, 1], axis = 0), label = '') # corrected
plt.show()